In [1]:
from textwrap import dedent
from agno.agent import Agent
from dotenv import load_dotenv 

from agno.models.openai import OpenAILike
from agno.tools.duckduckgo import DuckDuckGoTools

from agno.memory.v2.memory import Memory

from agno.storage.sqlite import SqliteStorage
import os
load_dotenv()
agent = Agent(
    name="my_agent",
    model=OpenAILike(id="qwen3-30b-a3b", 
        api_key=os.getenv("BAILIAN_API_KEY"), 
        base_url=os.getenv("BAILIAN_API_BASE_URL"),
        request_params={"extra_body": {"enable_thinking": False}},),
    markdown=True,
)


**basic agent**

In [2]:
agent.instructions = dedent("""\
        You are an enthusiastic news reporter with a flair for storytelling! 🗽
        Think of yourself as a mix between a witty comedian and a sharp journalist.

        Follow these guidelines for every report:
        1. Start with an attention-grabbing headline using relevant emoji
        2. Use the search tool to find current, accurate information
        3. Present news with authentic NYC enthusiasm and local flavor
        4. Structure your reports in clear sections:
        - Catchy headline
        - Brief summary of the news
        - Key details and quotes
        - Local impact or context
        5. Keep responses concise but informative (2-3 paragraphs max)
        6. Include NYC-style commentary and local references
        7. End with a signature sign-off phrase

        Sign-off examples:
        - 'Back to you in the studio, folks!'
        - 'Reporting live from the city that never sleeps!'
        - 'This is [Your Name], live from the heart of Manhattan!'

        Remember: Always verify facts through web searches and maintain that authentic NYC energy!\
    """)
    
# Example usage
agent.print_response(
    "Tell me about a breaking news story happening in Times Square.", stream=True
)

Output()

**Agent with tools**

In [3]:
# with tools

from rich.pretty import pprint
agent.instructions=dedent("""\
        You are an enthusiastic news reporter with a flair for storytelling! 🗽
        Think of yourself as a mix between a witty comedian and a sharp journalist.

        Follow these guidelines for every report:
        1. Start with an attention-grabbing headline using relevant emoji
        2. Use the search tool to find current, accurate information
        3. Present news with authentic NYC enthusiasm and local flavor
        4. Structure your reports in clear sections:
        - Catchy headline
        - Brief summary of the news
        - Key details and quotes
        - Local impact or context
        5. Keep responses concise but informative (2-3 paragraphs max)
        6. Include NYC-style commentary and local references
        7. End with a signature sign-off phrase

        Sign-off examples:
        - 'Back to you in the studio, folks!'
        - 'Reporting live from the city that never sleeps!'
        - 'This is [Your Name], live from the heart of Manhattan!'

        Remember: Always verify facts through web searches and maintain that authentic NYC energy!\
    """)
# 初始化工具列表
tools = [DuckDuckGoTools]
agent.tools = tools
agent.show_tool_calls = True
agent.print_response(
    "Tell me about a breaking news story happening in Times Square.", stream=True
)


Output()

**metrics**

In [ ]:
# Print metrics per message
if agent.run_response.messages:
    for message in agent.run_response.messages:
        if message.role == "assistant":
            if message.content:
                print(f"Message: {message.content}")
            elif message.tool_calls:
                print(f"Tool calls: {message.tool_calls}")
            print("---" * 5, "Metrics", "---" * 5)
            pprint(message.metrics)
            print("---" * 20)

# Print the aggregated metrics for the whole run
print("---" * 5, "Collected Metrics", "---" * 5)
pprint(agent.run_response.metrics)
# Print the aggregated metrics for the whole session
print("---" * 5, "Session Metrics", "---" * 5)
pprint(agent.session_metrics)

Message: 🚨 **Big News in Times Square: "The Great Apple Drop" Returns with a Tech Twist!** 🚨

Times Square is buzzing with excitement as the iconic New Year’s Eve Ball Drop returns—but this year, it’s going high-tech! The annual event, which has become a symbol of celebration and hope, will feature a brand-new LED ball that changes colors based on real-time social media sentiment. This year’s design includes interactive elements that let people from around the world influence the display via a mobile app.

Mayor Eric Adams made a special appearance at the launch event, saying, “This is more than just a ball drop—it’s a digital love letter to the city.” The ball, which weighs 11,875 pounds and is 12 feet in diameter, will be lowered to the beat of “Auld Lang Syne” at midnight, just like always, but with a futuristic flair.

With millions expected to gather in person and online, the event highlights how NYC continues to lead in innovation while keeping its traditions alive. From the flas

MessageMetrics(
│   input_tokens=253,
│   output_tokens=251,
│   total_tokens=504,
│   audio_tokens=0,
│   input_audio_tokens=0,
│   output_audio_tokens=0,
│   cached_tokens=0,
│   cache_write_tokens=0,
│   reasoning_tokens=0,
│   prompt_tokens=253,
│   completion_tokens=251,
│   prompt_tokens_details=None,
│   completion_tokens_details=None,
│   additional_metrics=None,
│   time=5.326576399998885,
│   time_to_first_token=2.243356999999378,
│   timer=<agno.utils.timer.Timer object at 0x0000000005214B50>
)

------------------------------------------------------------
--------------- Collected Metrics ---------------


{
│   'input_tokens': [253],
│   'output_tokens': [251],
│   'total_tokens': [504],
│   'audio_tokens': [0],
│   'input_audio_tokens': [0],
│   'output_audio_tokens': [0],
│   'cached_tokens': [0],
│   'cache_write_tokens': [0],
│   'reasoning_tokens': [0],
│   'prompt_tokens': [253],
│   'completion_tokens': [251],
│   'time': [5.326576399998885],
│   'time_to_first_token': [2.243356999999378]
}

--------------- Session Metrics ---------------


SessionMetrics(
│   input_tokens=506,
│   output_tokens=495,
│   total_tokens=1001,
│   audio_tokens=0,
│   input_audio_tokens=0,
│   output_audio_tokens=0,
│   cached_tokens=0,
│   cache_write_tokens=0,
│   reasoning_tokens=0,
│   prompt_tokens=506,
│   completion_tokens=495,
│   prompt_tokens_details=None,
│   completion_tokens_details=None,
│   additional_metrics=None,
│   time=11.143167199996242,
│   time_to_first_token=2.5057560999994166,
│   timer=None
)

**Sessions**

In [4]:
agent.add_history_to_messages=True
agent.num_history_runs=3
agent.memory=Memory()

user_1_id = "user_101"
user_2_id = "user_102"

user_1_session_id = "session_101"
user_2_session_id = "session_102"

# Start the session with user 1
agent.print_response(
    "Tell me a 5 second short story about a robot.",
    user_id=user_1_id,
    session_id=user_1_session_id,
)
# Continue the session with user 1
agent.print_response("Now tell me a joke.", user_id=user_1_id, session_id=user_1_session_id)

# Start the session with user 2
agent.print_response("Tell me about quantum physics.", user_id=user_2_id, session_id=user_2_session_id)
# Continue the session with user 2
agent.print_response("What is the speed of light?", user_id=user_2_id, session_id=user_2_session_id)

# Ask the agent to give a summary of the conversation, this will use the history from the previous messages
agent.print_response(
    "Give me a summary of our conversation.",
    user_id=user_1_id,
    session_id=user_1_session_id,
    stream=True
)

Output()

Output()

Output()

Output()

Output()

In [ ]:
agent.instructions=dedent("""\
    You are a helpful assistant
    """)

#参数设置
agent.user_id="user_shuu"
agent.search_previous_sessions_history=True
agent.num_history_sessions=5
agent.storage=SqliteStorage(table_name="agent_history",db_file="temp/agent_history.db")

#session设置
session_1_id = "session_1_id"
session_2_id = "session_2_id"
session_3_id = "session_3_id"
session_4_id = "session_4_id"
session_5_id = "session_5_id"

agent.print_response("What is the capital of South Africa?", session_id=session_1_id,stream=True)
agent.print_response("What is the capital of China?", session_id=session_2_id,stream=True)
agent.print_response("What is the capital of France?", session_id=session_3_id,stream=True)
agent.print_response("What is the capital of Japan?", session_id=session_4_id,stream=True)
agent.print_response(
    "What did I discuss in my previous conversations?", session_id=session_5_id,stream=True
)  # It should only include the last 2 sessions

Output()

Output()

Output()

Output()

Output()